### Import Library

In [821]:
import numpy as np 
import pandas as pd
from bs4 import BeautifulSoup
import requests
import folium # map rendering library
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize


In [822]:
CLIENT_ID = 'HYPHVSN5ZS2JQW33YVJPOJIFPIWQHF40JSIFJYCPO1MJLTVT' # your Foursquare ID
CLIENT_SECRET = 'CUAOMPRHQQMT4LNHU2RDPYFTNGZJ4WK5F2ISGRABAWHJYE3G' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)
address = 'Hong Kong'

# geolocator = Nominatim(user_agent="foursquare_agent")
# location = geolocator.geocode(address)
latitude = 22.25
longitude = 114.16667
print(latitude, longitude)

Your credentails:
CLIENT_ID: HYPHVSN5ZS2JQW33YVJPOJIFPIWQHF40JSIFJYCPO1MJLTVT
CLIENT_SECRET:CUAOMPRHQQMT4LNHU2RDPYFTNGZJ4WK5F2ISGRABAWHJYE3G
22.25 114.16667


In [1111]:
# # create a hk_restaurant to store all the calling results
# hk_restaurant = pd.DataFrame()

# -------18 districts name :--------
# districts = {'Yuen Long','Central and Western',
# 'Eastern',
# 'Islands',
# 'Kowloon City',
# 'Kwai Tsing',
# 'Kwun Tong',
# 'North',
# 'Sai Kung',
# 'Sha Tin',
# 'Sham Shui Po',
# 'Southern',
# 'Tai Po',
# 'Tsuen Wan',
# 'Tuen Mun',
# 'Wan Chai',
# 'Wong Tai Sin',
# 'Yau Tsim Mong'}



# ----------- Kwun Tong Line + Island Line ------------
# Whampoa -> HUNG HOM 
# HKU -> Pok Fu Lam/SHEK TONG TSUI
# Wan Chai -> Wanchai
# Central -> CENTRAL,HK
# Wong Tai Sin -> CHUK YUEN
# Kowloon -> Austin
#  Olympic-> Olympic,hk

districts = {'HUNG HOM',
'Ho Man Tin',
'Yau Ma Tei',
'Mong Kok',
'Prince Edward',
'Shek Kip Mei',
'Kowloon Tong',
'Lok Fu',
'CHUK YUEN',
'Diamond Hill',
'Choi Hung',
'Kowloon Bay',
'Ngau Tau Kok',
'Kwun Tong',
'Lam Tin',
'Yau Tong',
'Tiu Keng Leng',
'Kennedy Town',
'SHEK TONG TSUI',
'Sai Ying Pun',
'Sheung Wan',
'CENTRAL,HK',
'Admiralty',
'Wanchai',
'Causeway Bay',
'Tin Hau',
'Fortress Hill',
'North Point',
'Quarry Bay',
'Tai Koo',
'Sai Wan Ho',
'Shau Kei Wan',
'Heng Fa Chuen',
'Chai Wan',
'Olympic,hk',
'Tsim Sha Tsui',
'Kowloon'
}

# districts = {'Tsim Sha Tsui'}

In [1112]:

def restaruant_api ( NEAR = None ):
    #categoryid 4d4b7105d754a06374d81259 is food
    categoryId = '4d4b7105d754a06374d81259'
    radius = 900
    limit = 500
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&near={}&v={}&categoryId={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET,NEAR, VERSION, categoryId, radius,limit)
    url

    results = requests.get(url).json()
    # assign relevant part of JSON to venues
    print( NEAR,':' )
    venues = results['response']['venues']
    # tranform venues into a dataframe
    
    dataframe = json_normalize(venues)
    if(dataframe.shape[0] < 1):
        return  pd.DataFrame()
    dataframe.head()
    dataframe['categories'] = dataframe['categories'].apply(lambda x : x[0]['name'])
    dataframe['near'] = NEAR
    return dataframe


In [1113]:
# print(dataframe.groupby('categories').count()) 
# print(dataframe.describe()) 
dfs = []
for district_name in districts:
    dataframe = restaruant_api(district_name)
    dfs.append(dataframe)

hk_restaurant = pd.concat(dfs,axis = 0,sort= True)
    

Choi Hung :
Admiralty :
Yau Ma Tei :
Fortress Hill :
Kowloon Bay :
Lok Fu :
Sheung Wan :
Tai Koo :
SHEK TONG TSUI :
Olympic,hk :
CENTRAL,HK :
Wanchai :
Kowloon Tong :
Ngau Tau Kok :
Causeway Bay :
CHUK YUEN :
HUNG HOM :
Kwun Tong :
Quarry Bay :
Chai Wan :
Tin Hau :
Shau Kei Wan :
Ho Man Tin :
Tiu Keng Leng :
Sai Wan Ho :
Tsim Sha Tsui :
Sai Ying Pun :
Kennedy Town :
Yau Tong :
Shek Kip Mei :
Kowloon :
Lam Tin :
Diamond Hill :
Heng Fa Chuen :
Mong Kok :
North Point :
Prince Edward :


In [1114]:
# dfs 
# Data punching : without coffe shope
# hk_restaurant = hk_restaurant[hk_restaurant['categories'] != 'Coffee Shop' ]
# hk_restaurant = hk_restaurant[hk_restaurant['categories'] != 'Café' ]
# hk_restaurant = hk_restaurant[hk_restaurant['categories'] != 'Fast Food Restaurant' ]
hk_restaurant = hk_restaurant[hk_restaurant['near'] != 'Tiu Keng Leng' ]


hk_restaurant

categories  hasPerk                        id  \
0          Sushi Restaurant    False  4fbccd90e4b0cc7b016710e1   
1               Snack Place    False  59e08bd0d48ec13960d661c6   
2              Noodle House    False  4ceddf0a62ef6dcbc5a9f559   
3                      Café    False  4b9de486f964a520b7c136e3   
4        Dim Sum Restaurant    False  4f1ac1a9e4b04ae08259fd4f   
5          Sushi Restaurant    False  4c56ab437329c92806038d80   
6      Hong Kong Restaurant    False  54045dd8498eae2180814d88   
7            Cha Chaan Teng    False  4b2c6e70f964a52005c724e3   
8      Cantonese Restaurant    False  4d4e39d423a76dcb1a365ddc   
9       Japanese Restaurant    False  50e90b03e4b0d1b6cd07eecc   
10     Fast Food Restaurant    False  4ce8c72094daa09031751d29   
11       Chinese Restaurant    False  4bffb03ec30a2d7f2943111d   
12     Cantonese Restaurant    False  4c9592786b35a1437dcb26dc   
13           Cha Chaan Teng    False  5587ad00498edb8f0fcb97db   
14                    Diner    False  52a4437a11d28c7fd7b7c89c   
15     Fast Food Restaurant    False  4c8d85f75e38b1f7110e3bf9   
16      Shanghai Restaurant    False  522d56ff11d2740eb21048d9   
17     Cantonese Restaurant    False  53526106498e0de0062c1895   
18     Fast Food Restaurant    False  4cb3619edd619c74e8bbe590   
19                   Bakery    False  4d590b1ffe7c224ba94673b5   
20     Fast Food Restaurant    False  53c3a336498e03a1e165b15c   
21               Steakhouse    False  53ac0584498e831970e320e7   
22           Cha Chaan Teng    False  4cbaa2dd035d236ae9b9db4e   
23              Coffee Shop    False  4eab9511991107f63ca9b58a   
24     Taiwanese Restaurant    False  50e29f60e4b0073ebe84e5e7   
25           Cha Chaan Teng    False  4ce2133daba88cfab53c59d7   
26               Restaurant    False  598952f6e97dfb6a157cbd48   
27       Chinese Restaurant    False  4c18571e1436a5935f488d75   
28           Ice Cream Shop    False  4d4bc03657b2a1cd6881e982   
29          Udon Restaurant    False  4be40a702457a5937ea6a915   
..                      ...      ...                       ...   
20           Sandwich Place    False  595a28892be425119f837ba5   
21             Noodle House    False  56c5b601cd10315dbbdd0591   
22              Coffee Shop    False  4fa8729ce4b0f0ac1d5eef81   
23     Cantonese Restaurant    False  506986d7e4b02c5032538694   
24     Taiwanese Restaurant    False  4c050cef187ec92885d1b77b   
25     Fast Food Restaurant    False  4c007989ad15a593f2068e73   
26       Donburi Restaurant    False  4c0598508f8fa5936e1cf20d   
27     Fast Food Restaurant    False  4ce405d9c46e6dcbb44dd915   
28       Chinese Restaurant    False  4c74689344d395214899f4be   
29     Hong Kong Restaurant    False  4bffbe7c92a6c92810fe42e2   
30     Cantonese Restaurant    False  4bd28ec5046076b052567471   
31     Fast Food Restaurant    False  4e2660dab0fb1fae1dd39cad   
32             Noodle House    False  53783081498e21d3bd510afd   
33                     Café    False  53c24343498ecf59cb04d967   
34     Hong Kong Restaurant    False  4c09140cffb8c9b6f5386961   
35     Cantonese Restaurant    False  528ed56d11d21d7ad78d61cd   
36                   Bakery    False  4c7daa19724976b0dc0ca30a   
37      Japanese Restaurant    False  4fdc10c1e4b07b2b8654d2e1   
38     Fast Food Restaurant    False  4c31b6fbed37a593e9b56a03   
39     Fast Food Restaurant    False  4e9ec42d1081a02e6380e587   
40              Coffee Shop    False  4b0eeaf5f964a520c75c23e3   
41  New American Restaurant    False  55c3395c498ea36597834f57   
42     Fast Food Restaurant    False  4bac05d7f964a520c8de3ae3   
43              Coffee Shop    False  4b2dc63bf964a52043db24e3   
44           Cha Chaan Teng    False  552e4cbc498e4b1d1244663f   
45     Fast Food Restaurant    False  4be25bd9d27a20a1738c8f5b   
46                     Café    False  546c2d73498e0d698cc429e1   
47          Thai Restaurant    False  55d95594498e93a180735873   
48                     Café    False  4d1196f53e33b60c106

In [1115]:
restauran_df =hk_restaurant[['name','location.lat','location.lng','categories']]

In [1116]:
food_map = folium.Map(location=[latitude, longitude], zoom_start=12)

In [1117]:
# add markers to map
for lat, lng, name, categories in zip(restauran_df['location.lat'], restauran_df['location.lng'], restauran_df['name'], restauran_df['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(food_map)  

food_map

In [1142]:
# overwhiling number of coffe shop
restauran_df.groupby('categories').count().sort_values(by=['name'],ascending=False)


name  location.lat  location.lng
categories                                                 
Coffee Shop                 207           207           207
Fast Food Restaurant        151           151           151
Chinese Restaurant          124           124           124
Cha Chaan Teng              121           121           121
Café                        106           106           106
Cantonese Restaurant         93            93            93
Hong Kong Restaurant         92            92            92
Noodle House                 80            80            80
Japanese Restaurant          57            57            57
Dim Sum Restaurant           52            52            52
Dessert Shop                 34            34            34
Italian Restaurant           31            31            31
Bakery                       29            29            29
Sushi Restaurant             27            27            27
Taiwanese Restaurant         26            26            26
Seafood Restaurant           26            26            26
Thai Restaurant              24            24            24
Vietnamese Restaurant        23            23            23
Restaurant                   23            23            23
Sandwich Place               21            21            21
Burger Joint                 21            21            21
Shanghai Restaurant          20            20            20
Snack Place                  19            19            19
Bubble Tea Shop              17            17            17
Pizza Place                  17            17            17
Asian Restaurant             15            15            15
Food Court                   14            14            14
Ramen Restaurant             13            13            13
American Restaurant          13            13            13
Ice Cream Shop               12            12            12
...                         ...           ...           ...
Hunan Restaurant              3             3             3
Bar                           3             3             3
Belgian Restaurant            3             3             3
Halal Restaurant              3             3             3
Hainan Restaurant             3             3             3
Bistro                        3             3             3
Spanish Restaurant            2             2             2
Taco Place                    2             2             2
Tapas Restaurant              2             2             2
Shabu-Shabu Restaurant        2             2             2
Fish Market                   2             2             2
Flower Shop                   2             2             2
Japanese Curry Restaurant     2             2             2
Turkish Restaurant            1             1             1
Fish & Chips Shop             1             1             1
Beer Bar                      1             1             1
Lounge                        1             1             1
Frozen Yogurt Shop            1             1             1
Supermarket                   1             1             1
Food & Drink Shop             1             1             1
Soup Place                    1             1             1
Kebab Restaurant              1             1             1
Furniture / Home Store        1             1             1
German Restaurant             1             1             1
Scandinavian Restaurant       1             1             1
Satay Restaurant              1             1             1
Hawaiian Restaurant           1             1             1
Hookah Bar                    1             1             1
Hot Dog Joint                 1             1             1
Hotel Bar                     1             1             1

[93 rows x 3 columns]

In [1119]:
hk_restaurant.groupby('near').count()

categories  hasPerk  id  location.address  location.cc  \
near                                                                     
Admiralty               50       50  50                50           50   
CENTRAL,HK              50       50  50                50           50   
CHUK YUEN               50       50  50                48           50   
Causeway Bay            50       50  50                49           50   
Chai Wan                50       50  50                48           50   
Choi Hung               50       50  50                49           50   
Diamond Hill            50       50  50                49           50   
Fortress Hill           50       50  50                50           50   
HUNG HOM                50       50  50                47           50   
Heng Fa Chuen           49       49  49                48           49   
Ho Man Tin              50       50  50                48           50   
Kennedy Town            50       50  50                49           50   
Kowloon                 50       50  50                47           50   
Kowloon Bay             50       50  50                49           50   
Kowloon Tong            50       50  50                49           50   
Kwun Tong               50       50  50                48           50   
Lam Tin                 50       50  50                48           50   
Lok Fu                  50       50  50                49           50   
Mong Kok                50       50  50                50           50   
Ngau Tau Kok            50       50  50                48           50   
North Point             50       50  50                49           50   
Olympic,hk              50       50  50                50           50   
Quarry Bay              50       50  50                48           50   
SHEK TONG TSUI          50       50  50                50           50   
Sai Wan Ho              50       50  50                49           50   
Sai Ying Pun            50       50  50                50           50   
Shau Kei Wan            50       50  50                48           50   
Shek Kip Mei            50       50  50                50           50   
Sheung Wan              50       50  50                50           50   
Tai Koo                 50       50  50                48           50   
Tin Hau                 50       50  50                50           50   
Tsim Sha Tsui           50       50  50                49           50   
Wanchai                 50       50  50                49           50   
Yau Ma Tei              50       50  50                50           50   
Yau Tong                49       49  49                44           49   

                location.city  location.country  location.crossStreet  \
near                                                                    
Admiralty                  50                50                    12   
CENTRAL,HK                 50                50                    12   
CHUK YUEN                  44                50                     3   
Causeway Bay               49                50                     3   
Chai Wan                   48                50                     3   
Choi Hung                  43                50                     3   
Diamond Hill               43                50                     1   
Fortress Hill              50                50                     1   
HUNG HOM                   47                50                     4   
Heng Fa Chuen              46                49                     1   
Ho Man Tin                 46                50                     3   
Kennedy Town               48                50                     6   
Kowloon                    44                50                     4   
Kowloon Bay                47                50                     1   
Kowloon Tong               44                50                     3   
Kwun Tong                  45       

# One-Hot encoding

In [1120]:
# one hot encoding
restaurant_cat_onehot = pd.get_dummies(hk_restaurant[['categories']], prefix="", prefix_sep="")
# add Near column back to dataframe
restaurant_cat_onehot['Near'] = hk_restaurant['near'] 
# move Near column to the first column
fixed_columns = [restaurant_cat_onehot.columns[-1]] + list(restaurant_cat_onehot.columns[:-1])
restaurant_cat_onehot = restaurant_cat_onehot[fixed_columns]


And let's examine the new dataframe size.

In [1121]:
restaurant_cat_onehot.shape

(1748, 94)

In [1122]:
restaurant_group = restaurant_cat_onehot.groupby('Near').mean().reset_index()
restaurant_group

Near  American Restaurant  Asian Restaurant  \
0        Admiralty                 0.02          0.020000   
1       CENTRAL,HK                 0.02          0.020000   
2        CHUK YUEN                 0.00          0.020000   
3     Causeway Bay                 0.00          0.000000   
4         Chai Wan                 0.00          0.020000   
5        Choi Hung                 0.00          0.020000   
6     Diamond Hill                 0.00          0.000000   
7    Fortress Hill                 0.00          0.000000   
8         HUNG HOM                 0.00          0.000000   
9    Heng Fa Chuen                 0.00          0.040816   
10      Ho Man Tin                 0.00          0.020000   
11    Kennedy Town                 0.04          0.020000   
12         Kowloon                 0.00          0.020000   
13     Kowloon Bay                 0.04          0.040000   
14    Kowloon Tong                 0.02          0.000000   
15       Kwun Tong                 0.00          0.000000   
16         Lam Tin                 0.02          0.000000   
17          Lok Fu                 0.00          0.000000   
18        Mong Kok                 0.00          0.000000   
19    Ngau Tau Kok                 0.00          0.020000   
20     North Point                 0.00          0.000000   
21      Olympic,hk                 0.00          0.000000   
22      Quarry Bay                 0.02          0.000000   
23  SHEK TONG TSUI                 0.00          0.000000   
24      Sai Wan Ho                 0.02          0.000000   
25    Sai Ying Pun                 0.00          0.000000   
26    Shau Kei Wan                 0.00          0.020000   
27    Shek Kip Mei                 0.00          0.000000   
28      Sheung Wan                 0.02          0.020000   
29         Tai Koo                 0.02          0.000000   
30         Tin Hau                 0.00          0.000000   
31   Tsim Sha Tsui                 0.02          0.000000   
32         Wanchai                 0.00          0.000000   
33      Yau Ma Tei                 0.00          0.000000   
34        Yau Tong                 0.00          0.000000   

    Australian Restaurant  BBQ Joint    Bakery   Bar  Beer Bar  \
0                    0.00       0.00  0.020000  0.02      0.00   
1                    0.02       0.00  0.020000  0.02      0.00   
2                    0.00       0.00  0.000000  0.00      0.00   
3                    0.00       0.00  0.000000  0.00      0.00   
4                    0.00       0.00  0.000000  0.00      0.00   
5                    0.00       0.00  0.020000  0.00      0.00   
6                    0.00       0.00  0.000000  0.00      0.00   
7                    0.00       0.04  0.000000  0.00      0.00   
8                    0.00       0.02  0.000000  0.00      0.00   
9                    0.00       0.00  0.020408  0.00      0.00   
10                   0.00       0.00  0.020000  0.00      0.02   
11                   0.02       0.00  0.020000  0.00      0.00   
12                   0.00       0.00  0.000000  0.00      0.00   
13                   0.00       0.02  0.000000  0.00      0.00   
14                   0.00       0.02  0.040000  0.00      0.00   
15                   0.00       0.00  0.020000  0.00      0.00   
16                   0.00       0.00  0.060000  0.00      0.00   
17                   0.00       0.00  0.020000  0.00      0.00   
18                   0.00       0.00  0.000000  0.00      0.00   
19                   0.00       0.02  0.020000  0.00      0.00   
20                   0.00       0.02  0.020000  0.00      0.00   
21                   0.00       0.00  0.020000  0.00      0.00   
22                   0.00       0.00  0.020000  0.00      0.00   
23                   0.02       0.00  0.040000  0.00      0.00   
24                   0.00       0.00  0.020000  0.00      0.00   
25                   0.00       0.00  0.040000  0.00      0.00   
26                   0.00       0.0

In [1123]:
num_top_resturant = 3

for hood in restaurant_group['Near']:
    print("----"+hood+"----")
    temp = restaurant_group[restaurant_group['Near'] == hood].T.reset_index()
    temp.columns = ['resturant','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_resturant))
    print('\n')

----Admiralty----
            resturant  freq
0                Café  0.16
1         Coffee Shop  0.16
2  Dim Sum Restaurant  0.08


----CENTRAL,HK----
            resturant  freq
0         Coffee Shop  0.18
1                Café  0.12
2  Dim Sum Restaurant  0.08


----CHUK YUEN----
            resturant  freq
0  Chinese Restaurant  0.14
1      Cha Chaan Teng  0.08
2         Coffee Shop  0.08


----Causeway Bay----
            resturant  freq
0         Coffee Shop  0.26
1  Chinese Restaurant  0.06
2      Cha Chaan Teng  0.06


----Chai Wan----
              resturant  freq
0    Chinese Restaurant  0.12
1  Hong Kong Restaurant  0.10
2  Fast Food Restaurant  0.10


----Choi Hung----
              resturant  freq
0  Fast Food Restaurant  0.12
1    Chinese Restaurant  0.10
2  Cantonese Restaurant  0.10


----Diamond Hill----
            resturant  freq
0      Cha Chaan Teng  0.14
1         Coffee Shop  0.10
2  Chinese Restaurant  0.10


----Fortress Hill----
              resturant  freq
0 

In [1124]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [1125]:



num_top_resturant = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Near']
for ind in np.arange(num_top_resturant):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
restaurant_group_sorted = pd.DataFrame(columns=columns)
restaurant_group_sorted['Near'] = restaurant_group['Near']

for ind in np.arange(restaurant_group.shape[0]):
    restaurant_group_sorted.iloc[ind, 1:] = return_most_common_venues(restaurant_group.iloc[ind, :], num_top_resturant)

restaurant_group_sorted.head()

Near 1st Most Common Venue 2nd Most Common Venue  \
0     Admiralty                  Café           Coffee Shop   
1    CENTRAL,HK           Coffee Shop                  Café   
2     CHUK YUEN    Chinese Restaurant  Cantonese Restaurant   
3  Causeway Bay           Coffee Shop        Cha Chaan Teng   
4      Chai Wan    Chinese Restaurant  Hong Kong Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Dim Sum Restaurant    Italian Restaurant  Fast Food Restaurant   
1    Dim Sum Restaurant    Italian Restaurant  Fast Food Restaurant   
2           Coffee Shop        Cha Chaan Teng    Dim Sum Restaurant   
3  Hong Kong Restaurant          Noodle House    Chinese Restaurant   
4  Fast Food Restaurant        Cha Chaan Teng            Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Noodle House  Cantonese Restaurant        Sandwich Place   
1          Noodle House  Cantonese Restaurant        Sandwich Place   
2                  Café   Japanese Restaurant           Pizza Place   
3  Cantonese Restaurant        Sandwich Place  Fast Food Restaurant   
4           Coffee Shop          Noodle House             Cafeteria   

  9th Most Common Venue 10th Most Common Venue  
0  Hong Kong Restaurant     Chinese Restaurant  
1  Hong Kong Restaurant     Chinese Restaurant  
2  Hong Kong Restaurant   Fast Food Restaurant  
3          Dessert Shop             Restaurant  
4  Cantonese Restaurant   Taiwanese Restaurant

# Clustering

In [1126]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

In [1127]:
# set number of clusters
kclusters = 5

restaurant_group_clustering = restaurant_group.drop('Near', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(restaurant_group_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 1, 0, 1, 1, 1, 1, 1, 3], dtype=int32)

In [1128]:
# restaurant_group_sorted =  restaurant_group_sorted.drop(columns = 'Cluster Labels') 

In [1129]:
# add clustering labels
restaurant_group_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [1130]:

restaurant_merged = hk_restaurant

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
restaurant_merged = restaurant_merged.join(restaurant_group_sorted.set_index('Near'), on='near')
restaurant_merged.head() # check the last columns!

categories  hasPerk                        id  \
0    Sushi Restaurant    False  4fbccd90e4b0cc7b016710e1   
1         Snack Place    False  59e08bd0d48ec13960d661c6   
2        Noodle House    False  4ceddf0a62ef6dcbc5a9f559   
3                Café    False  4b9de486f964a520b7c136e3   
4  Dim Sum Restaurant    False  4f1ac1a9e4b04ae08259fd4f   

                                location.address location.cc location.city  \
0          Shop DIH 10, MTR Diamond Hill Station          HK           钻石山   
1                                    彩虹邨商場 4 號地下          HK     Choi Hung   
2                                  Lung Chi Path          HK           NaN   
3  Shop 37, G/F, Kam Hon House, Choi Hung Estate          HK           NaN   
4          G/F., 22 Kam Pik House, Choi Hung Est          HK     Choi Hung   

  location.country location.crossStreet  \
0               香港                  NaN   
1               香港                  NaN   
2               香港                  NaN   
3               香港                  NaN   
4               香港                  NaN   

                           location.formattedAddress  \
0        [Shop DIH 10, MTR Diamond Hill Station, 香港]   
1                       [彩虹邨商場 4 號地下, Hong Kong, 香港]   
2                                [Lung Chi Path, 香港]   
3  [Shop 37, G/F, Kam Hon House, Choi Hung Estate...   
4    [G/F., 22 Kam Pik House, Choi Hung Est, 九龍, 香港]   

                             location.labeledLatLngs  ...  \
0  [{'label': 'display', 'lat': 22.34045029811581...  ...   
1  [{'label': 'display', 'lat': 22.334819, 'lng':...  ...   
2  [{'label': 'display', 'lat': 22.33612482170951...  ...   
3  [{'label': 'display', 'lat': 22.3359790359966,...  ...   
4  [{'label': 'display', 'lat': 22.33546993162889...  ...   

   1st Most Common Venue  2nd Most Common Venue 3rd Most Common Venue  \
0   Fast Food Restaurant     Chinese Restaurant  Cantonese Restaurant   
1   Fast Food Restaurant     Chinese Restaurant  Cantonese Restaurant   
2   Fast Food Restaurant     Chinese Restaurant  Cantonese Restaurant   
3   Fast Food Restaurant     Chinese Restaurant  Cantonese Restaurant   
4   Fast Food Restaurant     Chinese Restaurant  Cantonese Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Cha Chaan Teng  Hong Kong Restaurant      Sushi Restaurant   
1        Cha Chaan Teng  Hong Kong Restaurant      Sushi Restaurant   
2        Cha Chaan Teng  Hong Kong Restaurant      Sushi Restaurant   
3        Cha Chaan Teng  Hong Kong Restaurant      Sushi Restaurant   
4        Cha Chaan Teng  Hong Kong Restaurant      Sushi Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                  Café    Dim Sum Restaurant           Coffee Shop   
1                  Café    Dim Sum Restaurant           Coffee Shop   
2                  Café    Dim Sum Restaurant           Coffee Shop   
3                  Café    Dim Sum Restaurant           Coffee Shop   
4                  Café    Dim Sum Restaurant           Coffee Shop   

   10th Most Common Venue  
0     Japanese Restaurant  
1     Japanese Restaurant  
2     Japanese Restaurant  
3     Japanese Restaurant  
4     Japanese Restaurant  

[5 rows x 30 columns]

In [1131]:
restaurant_merged
# create map
restaurant_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi,cat,near,cluster in zip(restaurant_merged['location.lat'], restaurant_merged['location.lng'], restaurant_merged['name'],restaurant_merged['categories'], restaurant_merged['near'], restaurant_merged['Cluster Labels']):
    label = folium.Popup(str(poi) +' Near :' + str(near) +' Cat :' +str(cat) + ' Cluster :' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(restaurant_clusters)
       
restaurant_clusters

In [1132]:
# restaurant_merged.loc[restaurant_merged['Cluster Labels'] == 0, restaurant_merged.columns[[16]+list(range(19, restaurant_merged.shape[1]))]]
# restaurant_merged.columns
# restaurant_merged.columns

# restaurant_merged.loc[restaurant_merged['Cluster Labels'] == 0, restaurant_merged.columns[[16]+list(range(19, restaurant_merged.shape[1]))]]
restaurant_group_sorted.loc[restaurant_group_sorted['Cluster Labels'] == 0]




Cluster Labels            Near 1st Most Common Venue  \
3                0    Causeway Bay           Coffee Shop   
11               0    Kennedy Town           Coffee Shop   
23               0  SHEK TONG TSUI           Coffee Shop   
25               0    Sai Ying Pun           Coffee Shop   
27               0    Shek Kip Mei        Cha Chaan Teng   
30               0         Tin Hau           Coffee Shop   
31               0   Tsim Sha Tsui           Coffee Shop   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3         Cha Chaan Teng  Hong Kong Restaurant          Noodle House   
11        Cha Chaan Teng   American Restaurant    Dim Sum Restaurant   
23    Chinese Restaurant     French Restaurant  Fast Food Restaurant   
25  Cantonese Restaurant                  Café    Chinese Restaurant   
27           Coffee Shop          Dessert Shop          Noodle House   
30                  Café  Fast Food Restaurant        Cha Chaan Teng   
31        Cha Chaan Teng  Fast Food Restaurant          Noodle House   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3     Chinese Restaurant  Cantonese Restaurant        Sandwich Place   
11             Gastropub    Chinese Restaurant    Mexican Restaurant   
23             Gastropub    Mexican Restaurant    Dim Sum Restaurant   
25          Noodle House                Bakery     French Restaurant   
27           Snack Place  Hong Kong Restaurant                Bakery   
30    Chinese Restaurant       Bubble Tea Shop          Noodle House   
31       Bubble Tea Shop                  Café    Dim Sum Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3   Fast Food Restaurant          Dessert Shop             Restaurant  
11        Breakfast Spot                  Café   Fast Food Restaurant  
23                Bakery        Breakfast Spot   Cantonese Restaurant  
25    Italian Restaurant      Tapas Restaurant    Japanese Restaurant  
27  Fast Food Restaurant   Dumpling Restaurant     Dim Sum Restaurant  
30    Donburi Restaurant  Cantonese Restaurant    Japanese Restaurant  
31          Dessert Shop   Dumpling Restaurant    Shanghai Restaurant

In [1133]:
restaurant_group_sorted.loc[restaurant_group_sorted['Cluster Labels'] == 1]

Cluster Labels           Near 1st Most Common Venue 2nd Most Common Venue  \
2                1      CHUK YUEN    Chinese Restaurant  Cantonese Restaurant   
4                1       Chai Wan    Chinese Restaurant  Hong Kong Restaurant   
5                1      Choi Hung  Fast Food Restaurant    Chinese Restaurant   
6                1   Diamond Hill        Cha Chaan Teng           Coffee Shop   
7                1  Fortress Hill  Fast Food Restaurant        Cha Chaan Teng   
8                1       HUNG HOM           Coffee Shop  Fast Food Restaurant   
10               1     Ho Man Tin           Coffee Shop  Hong Kong Restaurant   
13               1    Kowloon Bay           Coffee Shop  Fast Food Restaurant   
15               1      Kwun Tong  Fast Food Restaurant        Cha Chaan Teng   
16               1        Lam Tin    Chinese Restaurant  Fast Food Restaurant   
18               1       Mong Kok           Coffee Shop  Fast Food Restaurant   
19               1   Ngau Tau Kok    Chinese Restaurant  Fast Food Restaurant   
20               1    North Point  Fast Food Restaurant        Cha Chaan Teng   
21               1     Olympic,hk  Fast Food Restaurant           Coffee Shop   
33               1     Yau Ma Tei           Coffee Shop  Fast Food Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2            Coffee Shop        Cha Chaan Teng    Dim Sum Restaurant   
4   Fast Food Restaurant        Cha Chaan Teng            Restaurant   
5   Cantonese Restaurant        Cha Chaan Teng  Hong Kong Restaurant   
6     Chinese Restaurant      Sushi Restaurant  Hong Kong Restaurant   
7            Coffee Shop          Noodle House                  Café   
8     Chinese Restaurant  Hong Kong Restaurant  Cantonese Restaurant   
10  Fast Food Restaurant  Cantonese Restaurant    Chinese Restaurant   
13    Chinese Restaurant          Noodle House  Cantonese Restaurant   
15           Coffee Shop    Chinese Restaurant  Cantonese Restaurant   
16  Hong Kong Restaurant        Cha Chaan Teng          Noodle House   
18  Hong Kong Restaurant  Cantonese Restaurant    Chinese Restaurant   
19                  Café   Japanese Restaurant          Noodle House   
20           Coffee Shop  Hong Kong Restaurant  Cantonese Restaurant   
21    Chinese Restaurant        Cha Chaan Teng    Dim Sum Restaurant   
33  Hong Kong Restaurant        Cha Chaan Teng    Chinese Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2                   Café   Japanese Restaurant           Pizza Place   
4            Coffee Shop          Noodle House             Cafeteria   
5       Sushi Restaurant                  Café    Dim Sum Restaurant   
6   Cantonese Restaurant                  Café    Dim Sum Restaurant   
7     Chinese Restaurant  Cantonese Restaurant             BBQ Joint   
8                   Café          Noodle House        Cha Chaan Teng   
10        Cha Chaan Teng    Italian Restaurant       Bubble Tea Shop   
13                  Café   Japanese Restaurant   Shanghai Restaurant   
15                  Café  Hong Kong Restaurant              Tea Room   
16                Bakery       Thai Restaurant   Japanese Restaurant   
18            Steakhouse    Dim Sum Restaurant   Japanese Restaurant   
19        Cha Chaan Teng  Cantonese Restaurant  Hong Kong Restaurant   
20                  Café   Japanese Restaurant    Donburi Restaurant   
21   Japanese Restaurant          Noodle House  Taiwanese Restaurant   
33          Noodle House  Cantonese Restaurant    Dim Sum Restaurant   

   9th Most Common Venue 10th Most Common Venue  
2   Hong Kong Restaurant   Fast Food Restaurant  
4   Cantonese Restaurant   Taiwanese Restaurant  
5            Coffee Shop    Japanese Restaurant  
6   Fast Food Restaurant           Noodle House  
7    Japanese Restaurant             Restaurant  
8       Sushi Restaurant    Japanese Restaurant  
10   Shanghai Restaurant      Hotpot Restaurant  
1

In [1134]:
restaurant_group_sorted.loc[restaurant_group_sorted['Cluster Labels'] == 2]

Cluster Labels          Near 1st Most Common Venue 2nd Most Common Venue  \
0                2     Admiralty                  Café           Coffee Shop   
1                2    CENTRAL,HK           Coffee Shop                  Café   
14               2  Kowloon Tong           Coffee Shop                  Café   
22               2    Quarry Bay  Fast Food Restaurant           Coffee Shop   
24               2    Sai Wan Ho           Coffee Shop  Fast Food Restaurant   
28               2    Sheung Wan           Coffee Shop                  Café   
29               2       Tai Koo           Coffee Shop  Cantonese Restaurant   
32               2       Wanchai                  Café           Coffee Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Dim Sum Restaurant    Italian Restaurant  Fast Food Restaurant   
1     Dim Sum Restaurant    Italian Restaurant  Fast Food Restaurant   
14    Chinese Restaurant        Cha Chaan Teng    Italian Restaurant   
22  Cantonese Restaurant   Japanese Restaurant  Hong Kong Restaurant   
24   Japanese Restaurant  Cantonese Restaurant                  Café   
28    Dim Sum Restaurant    Italian Restaurant          Noodle House   
29  Fast Food Restaurant   Japanese Restaurant  Hong Kong Restaurant   
32  Fast Food Restaurant           Pizza Place    Dim Sum Restaurant   

    6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0            Noodle House  Cantonese Restaurant         Sandwich Place   
1            Noodle House  Cantonese Restaurant         Sandwich Place   
14                 Bakery  Taiwanese Restaurant   Fast Food Restaurant   
22         Cha Chaan Teng                  Café  Vietnamese Restaurant   
24         Cha Chaan Teng  Hong Kong Restaurant     Dim Sum Restaurant   
28   Cantonese Restaurant  Hong Kong Restaurant    Japanese Restaurant   
29  Vietnamese Restaurant                  Café         Cha Chaan Teng   
32   Hong Kong Restaurant          Noodle House         Cha Chaan Teng   

   9th Most Common Venue   10th Most Common Venue  
0   Hong Kong Restaurant       Chinese Restaurant  
1   Hong Kong Restaurant       Chinese Restaurant  
14  Cantonese Restaurant               Restaurant  
22          Burger Joint     Taiwanese Restaurant  
24          Noodle House    Vietnamese Restaurant  
28  Fast Food Restaurant           Sandwich Place  
29  Taiwanese Restaurant  New American Restaurant  
32  Cantonese Restaurant           Sandwich Place

In [1135]:
restaurant_group_sorted.loc[restaurant_group_sorted['Cluster Labels'] == 3]

Cluster Labels           Near 1st Most Common Venue 2nd Most Common Venue  \
9                3  Heng Fa Chuen          Noodle House                  Café   
12               3        Kowloon    Chinese Restaurant          Noodle House   
17               3         Lok Fu        Cha Chaan Teng    Chinese Restaurant   
26               3   Shau Kei Wan        Cha Chaan Teng  Fast Food Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9     Chinese Restaurant  Fast Food Restaurant      Ramen Restaurant   
12        Cha Chaan Teng       Thai Restaurant           Coffee Shop   
17           Coffee Shop       Thai Restaurant  Cantonese Restaurant   
26          Noodle House          Dessert Shop    Chinese Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
9        Thai Restaurant  Hong Kong Restaurant  Cantonese Restaurant   
12          Dessert Shop  Fast Food Restaurant                  Café   
17          Dessert Shop          Noodle House          Burger Joint   
26  Hong Kong Restaurant                 Diner  Cantonese Restaurant   

   9th Most Common Venue 10th Most Common Venue  
9       Asian Restaurant           Dessert Shop  
12  Hong Kong Restaurant       Halal Restaurant  
17                Bakery   Fast Food Restaurant  
26     Indian Restaurant        Bubble Tea Shop

In [1136]:
restaurant_group_sorted.loc[restaurant_group_sorted['Cluster Labels'] == 4]

Cluster Labels      Near 1st Most Common Venue 2nd Most Common Venue  \
34               4  Yau Tong    Seafood Restaurant    Chinese Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
34  Fast Food Restaurant                  Café      Sushi Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
34  Hong Kong Restaurant        Cha Chaan Teng   Japanese Restaurant   

         9th Most Common Venue 10th Most Common Venue  
34  Modern European Restaurant           Dessert Shop

In [1137]:
restaurant_group_sorted.groupby('Cluster Labels').count()

Near  1st Most Common Venue  2nd Most Common Venue  \
Cluster Labels                                                       
0                  7                      7                      7   
1                 15                     15                     15   
2                  8                      8                      8   
3                  4                      4                      4   
4                  1                      1                      1   

                3rd Most Common Venue  4th Most Common Venue  \
Cluster Labels                                                 
0                                   7                      7   
1                                  15                     15   
2                                   8                      8   
3                                   4                      4   
4                                   1                      1   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                   7                      7   
1                                  15                     15   
2                                   8                      8   
3                                   4                      4   
4                                   1                      1   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                   7                      7   
1                                  15                     15   
2                                   8                      8   
3                                   4                      4   
4                                   1                      1   

                9th Most Common Venue  10th Most Common Venue  
Cluster Labels                                                 
0                                   7                       7  
1                                  15                      15  
2                                   8                       8  
3                                   4                       4  
4                                   1                       1

In [1138]:
restaurant_cat_onehot = pd.get_dummies(restaurant_merged[['categories']], prefix="", prefix_sep="")

restaurant_cat_onehot['Cluster Labels'] = restaurant_merged['Cluster Labels'] 
# move Near column to the first column
fixed_columns = [restaurant_cat_onehot.columns[-1]] + list(restaurant_cat_onehot.columns[:-1])
restaurant_cat_onehot = restaurant_cat_onehot[fixed_columns]

In [1139]:
restaurant_cluster = restaurant_cat_onehot.groupby('Cluster Labels').mean().reset_index()
restaurant_cluster

Cluster Labels  American Restaurant  Asian Restaurant  \
0               0             0.008571          0.002857   
1               1             0.004000          0.009333   
2               2             0.017500          0.007500   
3               3             0.000000          0.020101   
4               4             0.000000          0.000000   

   Australian Restaurant  BBQ Joint    Bakery     Bar  Beer Bar  \
0               0.005714   0.005714  0.022857  0.0000  0.000000   
1               0.000000   0.008000  0.012000  0.0000  0.001333   
2               0.005000   0.002500  0.022500  0.0075  0.000000   
3               0.000000   0.000000  0.010050  0.0000  0.000000   
4               0.000000   0.000000  0.020408  0.0000  0.000000   

   Beijing Restaurant  Belgian Restaurant  ...  Taco Place  \
0            0.008571              0.0000  ...    0.005714   
1            0.001333              0.0000  ...    0.000000   
2            0.007500              0.0075  ...    0.000000   
3            0.000000              0.0000  ...    0.000000   
4            0.000000              0.0000  ...    0.000000   

   Taiwanese Restaurant  Tapas Restaurant  Tea Room  Thai Restaurant  \
0              0.005714          0.005714  0.002857         0.005714   
1              0.018667          0.000000  0.005333         0.008000   
2              0.017500          0.000000  0.002500         0.002500   
3              0.010050          0.000000  0.000000         0.070352   
4              0.020408          0.000000  0.000000         0.020408   

   Turkish Restaurant  Udon Restaurant  Vegetarian / Vegan Restaurant  \
0            0.000000         0.000000                       0.008571   
1            0.001333         0.002667                       0.009333   
2            0.000000         0.000000                       0.000000   
3            0.000000         0.005025                       0.000000   
4            0.000000         0.000000                       0.000000   

   Vietnamese Restaurant  Wings Joint  
0               0.011429     0.005714  
1               0.014667     0.000000  
2               0.020000     0.000000  
3               0.000000     0.005025  
4               0.000000     0.000000  

[5 rows x 94 columns]

In [1140]:
num_top_resturant = 30

for hood in restaurant_cluster['Cluster Labels']:
    print("---- Cluster "+str(hood)+": ----")
    temp = restaurant_cluster[restaurant_cluster['Cluster Labels'] == hood].T.reset_index()
    temp.columns = ['resturant','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_resturant))
    print('\n')

---- Cluster 0: ----
                        resturant  freq
0                     Coffee Shop  0.20
1                  Cha Chaan Teng  0.06
2              Chinese Restaurant  0.05
3            Fast Food Restaurant  0.05
4                    Noodle House  0.05
5                            Café  0.04
6            Cantonese Restaurant  0.04
7              Dim Sum Restaurant  0.03
8                    Dessert Shop  0.03
9            Hong Kong Restaurant  0.03
10              French Restaurant  0.02
11             Italian Restaurant  0.02
12            Japanese Restaurant  0.02
13               Malay Restaurant  0.02
14            Dumpling Restaurant  0.02
15                      Gastropub  0.02
16                    Snack Place  0.02
17                         Bakery  0.02
18                 Sandwich Place  0.01
19             Mexican Restaurant  0.01
20              Hotpot Restaurant  0.01
21                 Ice Cream Shop  0.01
22              Indian Restaurant  0.01
23          Vietnam

### coffe shop cluster - office area
---- Cluster 0: ----
              resturant  freq
0           Coffee Shop  0.21
1                  Café  0.06
2    Italian Restaurant  0.06
3    Dim Sum Restaurant  0.06
4  Cantonese Restaurant  0.06

### Chinese food cluster - living area
---- Cluster 1: ----
              resturant  freq
0    Chinese Restaurant  0.14
1          Noodle House  0.08
2  Fast Food Restaurant  0.07
3        Cha Chaan Teng  0.06
4  Hong Kong Restaurant  0.06

### Fast food and chinese food cluster - shoping area
---- Cluster 2: ----
              resturant  freq
0  Fast Food Restaurant  0.10
1    Chinese Restaurant  0.08
2                  Café  0.07
3          Dessert Shop  0.06
4        Cha Chaan Teng  0.06

### Japanese food cluster - more japanese restaurant
---- Cluster 3: ----
              resturant  freq
0   Japanese Restaurant  0.13
1                  Café  0.10
2           Coffee Shop  0.10
3  Cantonese Restaurant  0.09
4  Fast Food Restaurant  0.06

### more food choices
---- Cluster 4: ----
              resturant  freq
0           Coffee Shop  0.11
1                  Café  0.08
2    Chinese Restaurant  0.07
3  Fast Food Restaurant  0.07
4  Cantonese Restaurant  0.05

In [1161]:
restauran_df.groupby('categories').count().sort_values(by=['name'],ascending=False)

name  location.lat  location.lng
categories                                                 
Coffee Shop                 207           207           207
Fast Food Restaurant        151           151           151
Chinese Restaurant          124           124           124
Cha Chaan Teng              121           121           121
Café                        106           106           106
Cantonese Restaurant         93            93            93
Hong Kong Restaurant         92            92            92
Noodle House                 80            80            80
Japanese Restaurant          57            57            57
Dim Sum Restaurant           52            52            52
Dessert Shop                 34            34            34
Italian Restaurant           31            31            31
Bakery                       29            29            29
Sushi Restaurant             27            27            27
Taiwanese Restaurant         26            26            26
Seafood Restaurant           26            26            26
Thai Restaurant              24            24            24
Vietnamese Restaurant        23            23            23
Restaurant                   23            23            23
Sandwich Place               21            21            21
Burger Joint                 21            21            21
Shanghai Restaurant          20            20            20
Snack Place                  19            19            19
Bubble Tea Shop              17            17            17
Pizza Place                  17            17            17
Asian Restaurant             15            15            15
Food Court                   14            14            14
Ramen Restaurant             13            13            13
American Restaurant          13            13            13
Ice Cream Shop               12            12            12
...                         ...           ...           ...
Hunan Restaurant              3             3             3
Bar                           3             3             3
Belgian Restaurant            3             3             3
Halal Restaurant              3             3             3
Hainan Restaurant             3             3             3
Bistro                        3             3             3
Spanish Restaurant            2             2             2
Taco Place                    2             2             2
Tapas Restaurant              2             2             2
Shabu-Shabu Restaurant        2             2             2
Fish Market                   2             2             2
Flower Shop                   2             2             2
Japanese Curry Restaurant     2             2             2
Turkish Restaurant            1             1             1
Fish & Chips Shop             1             1             1
Beer Bar                      1             1             1
Lounge                        1             1             1
Frozen Yogurt Shop            1             1             1
Supermarket                   1             1             1
Food & Drink Shop             1             1             1
Soup Place                    1             1             1
Kebab Restaurant              1             1             1
Furniture / Home Store        1             1             1
German Restaurant             1             1             1
Scandinavian Restaurant       1             1             1
Satay Restaurant              1             1             1
Hawaiian Restaurant           1             1             1
Hookah Bar                    1             1             1
Hot Dog Joint                 1             1             1
Hotel Bar                     1             1             1

[93 rows x 3 columns]

In [1191]:
restaurant_punch = restaurant_merged
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Coffee Shop' ]
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Café' ]
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Fast Food Restaurant' ]
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Cha Chaan Teng' ]
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Chinese Restaurant' ]
restaurant_punch = restaurant_punch[restaurant_punch['categories'] != 'Hong Kong Restaurant' ]
# chinese_rest = restauran_df[restauran_df['categories']=='Dim Sum Restaurant']
# Japanese Restaurant
# French Restaurant
# Café

In [1192]:
food_map = folium.Map(location=[latitude, longitude], zoom_start=12)

In [1193]:
# add markers to map
for lat, lng, name, categories in zip(restaurant_punch['location.lat'], restaurant_punch['location.lng'], restaurant_punch['name'], restaurant_punch['categories']):
    label = '{}, {}'.format(name, categories)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(food_map)  

food_map

In [1194]:
restaurant_punch.shape

(947, 30)

## Get details information of the restaurants

In [1195]:
def try_catch(x,a):
    result = ''
    try: 
        result = x[a]
#         print('catch: ',result )
    except: 
        result = None
    return result


restaurant_punch['rating'] = ''
restaurant_punch['checkins'] = ''
restaurant_punch['price_tier'] = ''
restaurant_punch['price'] = ''
# restaurant_punch['attributes'] = ''

In [1196]:
restaurant_details = restaurant_punch
restaurant_details

categories  hasPerk                        id  \
0                Sushi Restaurant    False  4fbccd90e4b0cc7b016710e1   
1                     Snack Place    False  59e08bd0d48ec13960d661c6   
2                    Noodle House    False  4ceddf0a62ef6dcbc5a9f559   
4              Dim Sum Restaurant    False  4f1ac1a9e4b04ae08259fd4f   
5                Sushi Restaurant    False  4c56ab437329c92806038d80   
8            Cantonese Restaurant    False  4d4e39d423a76dcb1a365ddc   
9             Japanese Restaurant    False  50e90b03e4b0d1b6cd07eecc   
12           Cantonese Restaurant    False  4c9592786b35a1437dcb26dc   
14                          Diner    False  52a4437a11d28c7fd7b7c89c   
16            Shanghai Restaurant    False  522d56ff11d2740eb21048d9   
17           Cantonese Restaurant    False  53526106498e0de0062c1895   
19                         Bakery    False  4d590b1ffe7c224ba94673b5   
21                     Steakhouse    False  53ac0584498e831970e320e7   
24           Taiwanese Restaurant    False  50e29f60e4b0073ebe84e5e7   
26                     Restaurant    False  598952f6e97dfb6a157cbd48   
28                 Ice Cream Shop    False  4d4bc03657b2a1cd6881e982   
29                Udon Restaurant    False  4be40a702457a5937ea6a915   
31      Japanese Curry Restaurant    False  57654315498ead027e3e7f39   
33           Cantonese Restaurant    False  5b9a0fa5c8b2fb002caa30a8   
34  Vegetarian / Vegan Restaurant    False  4cfe2715feec6dcb1a245636   
35             Dim Sum Restaurant    False  572ef5d2498eedd42ba9a620   
36            Japanese Restaurant    False  5392eb6d498e932c3f097b9b   
39          Vietnamese Restaurant    False  58d9f86ec5f8a710c066902b   
41               Sushi Restaurant    False  5a6728489e0d5424e213d5b3   
43                     Food Court    False  4d9d636cc99fb60c3d71c68b   
44               Asian Restaurant    False  5b98ebba4a7aae002c9ac0c8   
47           Cantonese Restaurant    False  57d4ee97498ee2a966734fc2   
0                  Sandwich Place    False  4b1b34f3f964a52093f923e3   
1            Cantonese Restaurant    False  4b07a677f964a52033ff22e3   
2                    Burger Joint    False  5ae153b68ad62e00392d5a9c   
..                            ...      ...                       ...   
40                    Flower Shop    False  4d6f1b330187236ab7c897ba   
41             Beijing Restaurant    False  5117786ce4b00c1961fdeb42   
42                 Sandwich Place    False  57d4bade498e4af699d051c4   
43           Cantonese Restaurant    False  4c8b833b3dc2a1cd8bb3b632   
44                   Dessert Shop    False  4ce8a4f8d99f721eb80cb273   
45                         Buffet    False  4d830d3440a7a35d853eeebd   
0                     Snack Place    False  4c00e9a7ad15a593e6968e73   
2             Japanese Restaurant    False  4c88cca0944e224b1dee1e85   
4                    Burger Joint    False  50cfd8dc395044bed47554d9   
5               Hotpot Restaurant    False  4d1478dfbb488cfaa93997d4   
6              Donburi Restaurant    False  56aaf1a2498ef82f8520b195   
8                      Restaurant    False  5b50bf99dff815002bf6dfd5   
12                      BBQ Joint    False  5b8eb3693d4791002c427ae1   
16                    Salad Place    False  5b308506911fc4002cb60f79   
17             Dim Sum Restaurant    False  4fe53fa5e4b0c836716f6ea2   
18          Vietnamese Restaurant    False  5617bc3d498e7d9d92341e50   
19                   Dessert Shop    False  4c38665d6ec69c7480af04a9   
20                 Sandwich Place    False  595a28892be425119f837ba5   
21                   Noodle House    False  56c5b601cd10315dbbdd0591   
23           Cantonese Restaurant    False  506986d7e4b02c5032538694   
24           Taiwanese Restaurant    False  4c050cef187ec92885d1b77b   
26             Donburi Restaurant    False  4c0598508f8fa5936e1cf20d   
30           Cantonese Restaurant    False  4bd28ec5046076b052567471   
32                   Noodle House    False  53783081498e21d3bd5

In [1197]:
for index_label, row_series in restaurant_details.iterrows():
    url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(row_series['id'],CLIENT_ID, CLIENT_SECRET, VERSION)
    json = requests.get(url).json()
    venue = json['response']['venue']
    restaurant_details.at[index_label , 'rating'] = try_catch(venue,'rating')
    restaurant_details.at[index_label , 'price'] = try_catch(try_catch(venue,'price'),'message')
    restaurant_details.at[index_label , 'price_tier'] = try_catch(try_catch(venue,'price'),'tier')
    restaurant_details.at[index_label , 'checkins'] = try_catch(try_catch(venue,'stats'),'checkinsCount')
#     restaurant_details.at[index_label , 'attributes'] = try_catch(try_catch(venue,'attributes'),'groups')    
 
    
    
#     dataframe.at[index_label , 'respon'] = requests.get(url).json()
#     url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}&categoryId={}&radius={}&limit={}'.format(id,CLIENT_ID, CLIENT_SECRET, VERSION, categoryId, radius, LIMIT)


KeyError: 'venue'

In [1198]:
# url_df= url_df.drop(columns={'api_url'})
restaurant_details

categories  hasPerk                        id  \
0                Sushi Restaurant    False  4fbccd90e4b0cc7b016710e1   
1                     Snack Place    False  59e08bd0d48ec13960d661c6   
2                    Noodle House    False  4ceddf0a62ef6dcbc5a9f559   
4              Dim Sum Restaurant    False  4f1ac1a9e4b04ae08259fd4f   
5                Sushi Restaurant    False  4c56ab437329c92806038d80   
8            Cantonese Restaurant    False  4d4e39d423a76dcb1a365ddc   
9             Japanese Restaurant    False  50e90b03e4b0d1b6cd07eecc   
12           Cantonese Restaurant    False  4c9592786b35a1437dcb26dc   
14                          Diner    False  52a4437a11d28c7fd7b7c89c   
16            Shanghai Restaurant    False  522d56ff11d2740eb21048d9   
17           Cantonese Restaurant    False  53526106498e0de0062c1895   
19                         Bakery    False  4d590b1ffe7c224ba94673b5   
21                     Steakhouse    False  53ac0584498e831970e320e7   
24           Taiwanese Restaurant    False  50e29f60e4b0073ebe84e5e7   
26                     Restaurant    False  598952f6e97dfb6a157cbd48   
28                 Ice Cream Shop    False  4d4bc03657b2a1cd6881e982   
29                Udon Restaurant    False  4be40a702457a5937ea6a915   
31      Japanese Curry Restaurant    False  57654315498ead027e3e7f39   
33           Cantonese Restaurant    False  5b9a0fa5c8b2fb002caa30a8   
34  Vegetarian / Vegan Restaurant    False  4cfe2715feec6dcb1a245636   
35             Dim Sum Restaurant    False  572ef5d2498eedd42ba9a620   
36            Japanese Restaurant    False  5392eb6d498e932c3f097b9b   
39          Vietnamese Restaurant    False  58d9f86ec5f8a710c066902b   
41               Sushi Restaurant    False  5a6728489e0d5424e213d5b3   
43                     Food Court    False  4d9d636cc99fb60c3d71c68b   
44               Asian Restaurant    False  5b98ebba4a7aae002c9ac0c8   
47           Cantonese Restaurant    False  57d4ee97498ee2a966734fc2   
0                  Sandwich Place    False  4b1b34f3f964a52093f923e3   
1            Cantonese Restaurant    False  4b07a677f964a52033ff22e3   
2                    Burger Joint    False  5ae153b68ad62e00392d5a9c   
..                            ...      ...                       ...   
40                    Flower Shop    False  4d6f1b330187236ab7c897ba   
41             Beijing Restaurant    False  5117786ce4b00c1961fdeb42   
42                 Sandwich Place    False  57d4bade498e4af699d051c4   
43           Cantonese Restaurant    False  4c8b833b3dc2a1cd8bb3b632   
44                   Dessert Shop    False  4ce8a4f8d99f721eb80cb273   
45                         Buffet    False  4d830d3440a7a35d853eeebd   
0                     Snack Place    False  4c00e9a7ad15a593e6968e73   
2             Japanese Restaurant    False  4c88cca0944e224b1dee1e85   
4                    Burger Joint    False  50cfd8dc395044bed47554d9   
5               Hotpot Restaurant    False  4d1478dfbb488cfaa93997d4   
6              Donburi Restaurant    False  56aaf1a2498ef82f8520b195   
8                      Restaurant    False  5b50bf99dff815002bf6dfd5   
12                      BBQ Joint    False  5b8eb3693d4791002c427ae1   
16                    Salad Place    False  5b308506911fc4002cb60f79   
17             Dim Sum Restaurant    False  4fe53fa5e4b0c836716f6ea2   
18          Vietnamese Restaurant    False  5617bc3d498e7d9d92341e50   
19                   Dessert Shop    False  4c38665d6ec69c7480af04a9   
20                 Sandwich Place    False  595a28892be425119f837ba5   
21                   Noodle House    False  56c5b601cd10315dbbdd0591   
23           Cantonese Restaurant    False  506986d7e4b02c5032538694   
24           Taiwanese Restaurant    False  4c050cef187ec92885d1b77b   
26             Donburi Restaurant    False  4c0598508f8fa5936e1cf20d   
30           Cantonese Restaurant    False  4bd28ec5046076b052567471   
32                   Noodle House    False  53783081498e21d3bd5

In [1199]:
restaurant_details.to_csv('restaurant_price_clusters.csv')

In [1226]:
restaurant_details = pd.read_csv('restaurant_price_clusters.csv')

## Average restaruant price tier (0 - 3)

In [1227]:
restaurant_details['price_tier'].mean()

1.7520661157024793

In [1228]:
restaurant_details

Unnamed: 0                     categories  hasPerk  \
0             0               Sushi Restaurant    False   
1             1                    Snack Place    False   
2             2                   Noodle House    False   
3             4             Dim Sum Restaurant    False   
4             5               Sushi Restaurant    False   
5             8           Cantonese Restaurant    False   
6             9            Japanese Restaurant    False   
7            12           Cantonese Restaurant    False   
8            14                          Diner    False   
9            16            Shanghai Restaurant    False   
10           17           Cantonese Restaurant    False   
11           19                         Bakery    False   
12           21                     Steakhouse    False   
13           24           Taiwanese Restaurant    False   
14           26                     Restaurant    False   
15           28                 Ice Cream Shop    False   
16           29                Udon Restaurant    False   
17           31      Japanese Curry Restaurant    False   
18           33           Cantonese Restaurant    False   
19           34  Vegetarian / Vegan Restaurant    False   
20           35             Dim Sum Restaurant    False   
21           36            Japanese Restaurant    False   
22           39          Vietnamese Restaurant    False   
23           41               Sushi Restaurant    False   
24           43                     Food Court    False   
25           44               Asian Restaurant    False   
26           47           Cantonese Restaurant    False   
27            0                 Sandwich Place    False   
28            1           Cantonese Restaurant    False   
29            2                   Burger Joint    False   
..          ...                            ...      ...   
917          40                    Flower Shop    False   
918          41             Beijing Restaurant    False   
919          42                 Sandwich Place    False   
920          43           Cantonese Restaurant    False   
921          44                   Dessert Shop    False   
922          45                         Buffet    False   
923           0                    Snack Place    False   
924           2            Japanese Restaurant    False   
925           4                   Burger Joint    False   
926           5              Hotpot Restaurant    False   
927           6             Donburi Restaurant    False   
928           8                     Restaurant    False   
929          12                      BBQ Joint    False   
930          16                    Salad Place    False   
931          17             Dim Sum Restaurant    False   
932          18          Vietnamese Restaurant    False   
933          19                   Dessert Shop    False   
934          20                 Sandwich Place    False   
935          21                   Noodle House    False   
936          23           Cantonese Restaurant    False   
937          24           Taiwanese Restaurant    False   
938          26             Donburi Restaurant    False   
939          30           Cantonese Restaurant    False   
940          32                   Noodle House    False   
941          35           Cantonese Restaurant    False   
942          36                         Bakery    False   
943          37            Japanese Restaurant    False   
944          41        New American Restaurant    False   
945          47                Thai Restaurant    False   
946          49            Szechuan Restaurant    False   

                           id  \
0    4fbccd90e4b0cc7b016710e1   
1    59e08bd0d48ec13960d661c6   
2    4ceddf0a62ef6dcbc5a9f559   
3    4f1ac1a9e4b04ae08259fd4f   
4    4c56ab437329c92806038d80   
5    4d4e39d423a76dcb1a365ddc   
6    50e90b03e4b0d1b6cd07eecc   
7    4c9592786b35a1437dcb26dc   
8    52a4437a11d28c7fd7b7c89c   
9    522d56ff11d

In [1248]:
# create categories price_tier mean
# fill missing categories with mean 
price_categories_ref = restaurant_details.groupby('categories').mean()
price_categories_ref = price_categories_ref[ 'price_tier'].reset_index()
price_categories_ref = price_categories_ref.fillna(restaurant_details['price_tier'].mean())
price_categories_ref 



# price_categories_ref[price_categories_ref['categories'] =='American Restaurant ' ]
# restaurant_details.groupby('categories').count()
# price_cluster.sort_values(by=['price_tier'],ascending=False)

categories  price_tier
0             American Restaurant    2.000000
1                Asian Restaurant    1.400000
2           Australian Restaurant    1.666667
3                       BBQ Joint    2.000000
4                          Bakery    1.823529
5                             Bar    1.000000
6                        Beer Bar    1.752066
7              Beijing Restaurant    1.600000
8              Belgian Restaurant    1.000000
9                          Bistro    3.000000
10                 Breakfast Spot    2.000000
11                Bubble Tea Shop    2.090909
12                         Buffet    1.500000
13                   Burger Joint    1.769231
14                      Cafeteria    1.750000
15           Cantonese Restaurant    1.816327
16        Chinese Breakfast Place    2.000000
17                   Dessert Shop    1.636364
18             Dim Sum Restaurant    1.764706
19                          Diner    1.625000
20             Donburi Restaurant    1.571429
21            Dumpling Restaurant    2.000000
22             English Restaurant    1.750000
23              Fish & Chips Shop    1.752066
24                    Fish Market    1.000000
25                    Flower Shop    2.000000
26              Food & Drink Shop    1.752066
27                     Food Court    1.600000
28              French Restaurant    1.400000
29            Fried Chicken Joint    1.500000
..                            ...         ...
57     Modern European Restaurant    2.000000
58        New American Restaurant    2.000000
59                   Noodle House    1.734694
60                    Pizza Place    1.923077
61               Ramen Restaurant    1.428571
62                     Restaurant    1.750000
63                    Salad Place    1.666667
64                 Sandwich Place    1.615385
65               Satay Restaurant    2.000000
66        Scandinavian Restaurant    1.000000
67             Seafood Restaurant    1.500000
68         Shabu-Shabu Restaurant    2.000000
69            Shanghai Restaurant    1.857143
70                    Snack Place    1.400000
71                     Soup Place    2.000000
72             Spanish Restaurant    1.500000
73                     Steakhouse    2.166667
74                    Supermarket    1.752066
75               Sushi Restaurant    1.850000
76            Szechuan Restaurant    1.800000
77                     Taco Place    2.000000
78           Taiwanese Restaurant    1.666667
79               Tapas Restaurant    1.500000
80                       Tea Room    1.500000
81                Thai Restaurant    2.166667
82             Turkish Restaurant    2.000000
83                Udon Restaurant    1.500000
84  Vegetarian / Vegan Restaurant    1.500000
85          Vietnamese Restaurant    1.789474
86                    Wings Joint    1.500000

[87 rows x 2 columns]

In [1303]:
# price cleaning
restaurant_details_clean = restaurant_details[:0]
for cat in price_categories_ref['categories']:
    cat_mean = price_categories_ref.loc[price_categories_ref['categories'] == cat]['price_tier'].item()
    cat_clean_df = restaurant_details[restaurant_details['categories'] == cat]
    cat_clean_df = cat_clean_df.fillna( cat_mean)
#     cat_clean_df['price_tier_'] = cat_clean_col['price_tier']
    
#     print ('mean : ', cat_mean)
#     print (cat_clean_df['price_tier'])
#     price_categories_ref.loc[price_categories_ref['categories'] == cat, 'price_tier' ] 
    restaurant_details_clean = restaurant_details_clean.append(cat_clean_df)
#     restaurant_details_clean = restaurant_details_clean.append(restaurant_details[restaurant_details['categories'] == cat].fillna( price_categories_ref.loc[price_categories_ref['categories'] == cat, 'price_tier' ] ))



In [1304]:
restaurant_details_clean

Unnamed: 0                     categories  hasPerk  \
45           34            American Restaurant    False   
103           6            American Restaurant    False   
111          19            American Restaurant    False   
176          32            American Restaurant    False   
201          24            American Restaurant    False   
296          47            American Restaurant    False   
325           6            American Restaurant    False   
500          48            American Restaurant    False   
632          43            American Restaurant    False   
638           0            American Restaurant    False   
708          18            American Restaurant    False   
723          44            American Restaurant    False   
825          25            American Restaurant    False   
25           44               Asian Restaurant    False   
48           42               Asian Restaurant    False   
113          25               Asian Restaurant    False   
119          35               Asian Restaurant    False   
183          41               Asian Restaurant    False   
294          42               Asian Restaurant    False   
371          46               Asian Restaurant    False   
409          20               Asian Restaurant    False   
518          34               Asian Restaurant    False   
571          36               Asian Restaurant    False   
605          47               Asian Restaurant    False   
715          30               Asian Restaurant    False   
811          41               Asian Restaurant    False   
873          13               Asian Restaurant    False   
892          40               Asian Restaurant    False   
169          16          Australian Restaurant    False   
246          49          Australian Restaurant    False   
..          ...                            ...      ...   
680          25  Vegetarian / Vegan Restaurant    False   
718          34  Vegetarian / Vegan Restaurant    False   
815           4  Vegetarian / Vegan Restaurant    False   
849          16  Vegetarian / Vegan Restaurant    False   
22           39          Vietnamese Restaurant    False   
104           8          Vietnamese Restaurant    False   
198          13          Vietnamese Restaurant    False   
203          27          Vietnamese Restaurant    False   
204          28          Vietnamese Restaurant    False   
223           9          Vietnamese Restaurant    False   
330          15          Vietnamese Restaurant    False   
351          11          Vietnamese Restaurant    False   
418          35          Vietnamese Restaurant    False   
431          11          Vietnamese Restaurant    False   
451           3          Vietnamese Restaurant    False   
478           8          Vietnamese Restaurant    False   
479           9          Vietnamese Restaurant    False   
502           7          Vietnamese Restaurant    False   
509          17          Vietnamese Restaurant    False   
593          20          Vietnamese Restaurant    False   
609           3          Vietnamese Restaurant    False   
636          48          Vietnamese Restaurant    False   
649          14          Vietnamese Restaurant    False   
699           4          Vietnamese Restaurant    False   
765           8          Vietnamese Restaurant    False   
858          34          Vietnamese Restaurant    False   
932          18          Vietnamese Restaurant    False   
378           8                    Wings Joint    False   
540          18                    Wings Joint    False   
559          12                    Wings Joint    False   

                           id  \
45   4da9b8d64df01c19b177e096   
103  538315e5498e17831b272638   
111  5621df1d498e3dc5e7356f0f   
176  4da9b8d64df01c19b177e096   
201  58f4b23d1213843149aeaca3   
296  4da9b8d64df01c19b177e096   
325  4b096a6cf964a520fc1623e3   
500  58f4b23d1213843149aeaca3   
632  58f4b23d1213843149aeaca3   
638  58c95f06b50

In [1311]:
restaurant_details_clean.groupby('Cluster Labels').count()


Unnamed: 0  categories  hasPerk   id  location.address  \
Cluster Labels                                                           
0                      200         200      200  200               200   
1                      381         381      381  381               381   
2                      216         216      216  216               216   
3                      117         117      117  117               117   
4                       33          33       33   33                33   

                location.cc  location.city  location.country  \
Cluster Labels                                                 
0                       200            200               200   
1                       381            381               381   
2                       216            216               216   
3                       117            117               117   
4                        33             33                33   

                location.crossStreet  location.formattedAddress  ...  \
Cluster Labels                                                   ...   
0                                200                        200  ...   
1                                381                        381  ...   
2                                216                        216  ...   
3                                117                        117  ...   
4                                 33                         33  ...   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                 200                    200   
1                                 381                    381   
2                                 216                    216   
3                                 117                    117   
4                                  33                     33   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                 200                    200   
1                                 381                    381   
2                                 216                    216   
3                                 117                    117   
4                                  33                     33   

                9th Most Common Venue  10th Most Common Venue  rating  \
Cluster Labels                                                          
0                                 200                     200     200   
1                                 381                     381     381   
2                                 216                     216     216   
3                                 117                     117     117   
4                                  33                      33      33   

                checkins  price_tier  price  
Cluster Labels                               
0                    200         200    200  
1                    381         381    381  
2                    216         216    216  
3                    117         117    117  
4                     33          33     33  

[5 rows x 34 columns]

In [1312]:
restaurant_details.groupby('Cluster Labels').count()



Unnamed: 0  categories  hasPerk   id  location.address  \
Cluster Labels                                                           
0                      200         200      200  200               198   
1                      381         381      381  381               370   
2                      216         216      216  216               211   
3                      117         117      117  117               116   
4                       33          33       33   33                32   

                location.cc  location.city  location.country  \
Cluster Labels                                                 
0                       200            192               200   
1                       381            352               381   
2                       216            210               216   
3                       117            107               117   
4                        33             32                33   

                location.crossStreet  location.formattedAddress  ...  \
Cluster Labels                                                   ...   
0                                 14                        200  ...   
1                                 29                        381  ...   
2                                 23                        216  ...   
3                                  4                        117  ...   
4                                  0                         33  ...   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                 200                    200   
1                                 381                    381   
2                                 216                    216   
3                                 117                    117   
4                                  33                     33   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                 200                    200   
1                                 381                    381   
2                                 216                    216   
3                                 117                    117   
4                                  33                     33   

                9th Most Common Venue  10th Most Common Venue  rating  \
Cluster Labels                                                          
0                                 200                     200     125   
1                                 381                     381     228   
2                                 216                     216     136   
3                                 117                     117      77   
4                                  33                      33      22   

                checkins  price_tier  price  
Cluster Labels                               
0                      0         129    129  
1                      0         245    245  
2                      0         138    138  
3                      0          74     74  
4                      0          19     19  

[5 rows x 34 columns]

In [1331]:
from folium.plugins import HeatMap

In [1371]:
restaurant_details_list = restaurant_details_clean[restaurant_details_clean['price_tier'] > 1.5 ].fillna(0).values.tolist()

In [1378]:
lats = [float(item[11]) for item in restaurant_details_list]
lons = [float(item[12]) for item in restaurant_details_list]
mag = [float(item[33]/3*100) for item in restaurant_details_list]



In [1379]:
food_map = folium.Map(location=[latitude, longitude], zoom_start=12)
food_map.add_child(HeatMap(zip(lats, lons, mag), radius = 10))